In [1]:
import psycopg2
import pandas as pd
import matplotlib.pyplot as plt
import folium
import numpy as np
from shapely.wkt import loads
from geopy.distance import geodesic
from shapely.geometry import Point, Polygon
from sqlalchemy import create_engine
from shapely.geometry import Point, Polygon, LineString
import geopandas as gpd
import mplleaflet
import seaborn as sns

## Conect to database and import data

In [2]:
dias_da_semana = {
 'segunda': ['20240429', '20240506'],
 'terça': ['20240430', '20240507'],
 'quarta': ['20240424', '20240501', '20240508'],
 'quinta': ['20240425', '20240502', '20240509'],
 'sexta': ['20240426', '20240503', '20240510'],
 'sábado': ['20240427', '20240504', '20240511'],
 'domingo': ['20240428', '20240505']
}
linha_id = 606 
dia = 'segunda'

In [3]:
# Conectar ao banco de dados PostgreSQL
conn = psycopg2.connect(
    dbname="postgres",
    user="postgres",
    password="postgres",
    host="localhost",
    port="5432"
)

between_clauses = " OR ".join([f"(datahora BETWEEN '{data} 00:00:00' AND '{data} 23:59:59')" for data in dias_da_semana[dia]])

query = f'''select 
                *, 
                ST_Transform(geom::geometry, 4326) AS geometry 
            from vehicle_tracking_filtered where 
            linha = '{linha_id}' and ({between_clauses})
        '''

## Track the trajectory with Grids (483 example)

#### Generate grid for 422

In [4]:

# Load data into a GeoDataFrame
gdf = gpd.read_postgis(query, conn, geom_col='geometry', crs='EPSG:4326')

conn.close()


c:\Users\lucas\AppData\Local\Programs\Python\Python312\Lib\site-packages\geopandas\io\sql.py:170: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(


In [5]:
def create_grid(gdf=None, bounds=None, n_cells=10, overlap=False, crs="EPSG:4326"):

    import geopandas as gpd
    import shapely

    if bounds != None:
        xmin, ymin, xmax, ymax= bounds
    else:
        xmin, ymin, xmax, ymax= gdf.total_bounds

    # get cell size
    cell_size = (xmax-xmin)/n_cells
    # create the cells in a loop
    grid_cells = []
    for x0 in np.arange(xmin, xmax+cell_size, cell_size ):
        for y0 in np.arange(ymin, ymax+cell_size, cell_size):
            x1 = x0-cell_size
            y1 = y0+cell_size
            poly = shapely.geometry.box(x0, y0, x1, y1)
            #print (gdf.overlay(poly, how='intersection'))
            grid_cells.append( poly )

    cells = gpd.GeoDataFrame(grid_cells, columns=['geometry'],
                                     crs=crs)
    if overlap == True:
        cols = ['grid_id','geometry','grid_area']
        cells = cells.sjoin(gdf, how='inner').drop_duplicates('geometry')
    return cells

In [6]:
rio_minx, rio_miny = -43.7955, -23.0824
rio_maxx, rio_maxy = -43.1039, -22.7448

grid = create_grid(bounds=(rio_minx, rio_miny, rio_maxx, rio_maxy), n_cells=1500)
grid = grid.reset_index(names='grid_id')

In [7]:
grid.head()

grid_id                                           geometry
0        0  POLYGON ((-43.79596 -23.08240, -43.79596 -23.0...
1        1  POLYGON ((-43.79596 -23.08194, -43.79596 -23.0...
2        2  POLYGON ((-43.79596 -23.08148, -43.79596 -23.0...
3        3  POLYGON ((-43.79596 -23.08102, -43.79596 -23.0...
4        4  POLYGON ((-43.79596 -23.08056, -43.79596 -23.0...

## Search for outliers and Garage paths

In [8]:
def stat_day_per_line(gdf, grid):
    gdf.loc[:, 'datahora'] = pd.to_datetime(gdf['datahora'])
    gdf.loc[:, 'hour'] = gdf.loc[:, 'datahora'].dt.hour
    gdf = gdf.set_geometry('geometry')
    gdf.loc[:, 'save_geometry'] = gdf.loc[:, 'geometry']
    grid = grid.set_geometry('geometry')
    grid_joined = grid.sjoin(gdf, how='inner', predicate='contains')
    aggregated = grid_joined.groupby(['grid_id', 'geometry']).agg(
        count=('geometry', 'size'),
        median_time=('hour', 'median'),
        median_velocidade=('velocidade', 'median'),
        centroid=('save_geometry', lambda x: Point(x.x.mean(), x.y.mean()))
    ).reset_index()
 
    return aggregated


In [9]:
grids_stats = stat_day_per_line(gdf, grid)
grids_stats.shape

(2775, 6)

In [10]:
grids_stats

grid_id                                           geometry  count  \
0      694962  POLYGON ((-43.35979 -22.80668, -43.35979 -22.8...      1   
1      695698  POLYGON ((-43.35933 -22.80576, -43.35933 -22.8...      3   
2      697899  POLYGON ((-43.35795 -22.80622, -43.35795 -22.8...      1   
3      700102  POLYGON ((-43.35656 -22.80576, -43.35656 -22.8...      2   
4      701570  POLYGON ((-43.35564 -22.80576, -43.35564 -22.8...      1   
...       ...                                                ...    ...   
2770   999352  POLYGON ((-43.16845 -22.90812, -43.16845 -22.9...     49   
2771   999353  POLYGON ((-43.16845 -22.90766, -43.16845 -22.9...     31   
2772   999354  POLYGON ((-43.16845 -22.90719, -43.16845 -22.9...     23   
2773   999355  POLYGON ((-43.16845 -22.90673, -43.16845 -22.9...     18   
2774   999356  POLYGON ((-43.16845 -22.90627, -43.16845 -22.9...      3   

      median_time  median_velocidade                     centroid  
0            16.0                0.0  POINT (-43.35941 -22.80656)  
1            16.0                0.0  POINT (-43.35909 -22.80572)  
2            16.0               31.0  POINT (-43.35754 -22.80603)  
3            15.0               16.5  POINT (-43.35621 -22.80541)  
4            16.0               31.0  POINT (-43.35560 -22.80540)  
...           ...                ...                          ...  
2770         13.0               42.0  POINT (-43.16837 -22.90788)  
2771         13.0               40.0  POINT (-43.16838 -22.90750)  
2772         16.0               44.0  POINT (-43.16841 -22.90698)  
2773         15.0               48.0  POINT (-43.16842 -22.90652)  
2774         15.0               33.0  POINT (-43.16843 -22.90613)  

[2775 rows x 6 columns]

In [59]:
grid_filtered = grids_stats[(grids_stats['count'] > grids_stats['count'].quantile(0.5))   & (grids_stats['median_time'] > 10) & (grids_stats['median_time'] < 17) & (grids_stats['median_velocidade'] > 0)]

In [60]:
from sklearn.preprocessing import MinMaxScaler

def calculate_distance(point1, point2):
    return geodesic(point1, point2).meters


def normalize_column(df, column_name):
    scaler = MinMaxScaler()
    df[[column_name]] = scaler.fit_transform(df[[column_name]])
    return df

# Função para escolher o ponto final
def choose_end_point(grids_stats):
    candidates = grids_stats[(grids_stats['median_velocidade'] == 0) & (grids_stats['median_time'] > 10) & (grids_stats['median_time'] < 17)]
    initial_point = candidates.sort_values(by='count', ascending=False).head(1)
    start_point = initial_point['centroid'].values[0]

    candidates['start_distance'] = candidates['centroid'].apply(lambda x: calculate_distance((x.y, x.x), (start_point.y, start_point.x)))

    candidates = candidates[candidates['grid_id'] != initial_point['grid_id'].values[0]]
    # Normalizar as colunas 'count' e 'start_distance'
    candidates = normalize_column(candidates, 'count')
    candidates = normalize_column(candidates, 'start_distance')
    # Ajustar a fórmula para calcular 'combined' com mais peso em 'count'
    candidates['combined'] = (0.7 * candidates['count']) + (0.3 * candidates['start_distance'])

    # Escolher o ponto final com base na coluna 'combined'
    end_point = candidates.sort_values(by='combined', ascending=False).head(1)

    return start_point, end_point['centroid'].values[0]


In [62]:
start_point, end_point = choose_end_point(grids_stats)

C:\Users\lucas\AppData\Local\Temp\ipykernel_16968\202834735.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  candidates['start_distance'] = candidates['centroid'].apply(lambda x: calculate_distance((x.y, x.x), (start_point.y, start_point.x)))


In [63]:
map_center = [gdf['geometry'].y.mean(), gdf['geometry'].x.mean()]
m = folium.Map(location=map_center, zoom_start=15)

In [64]:

# Add grid cells to the map
for _, row in grid_filtered.iterrows():
    folium.GeoJson(row.geometry).add_to(m)
    folium.Marker(location=[row['geometry'].centroid.y, row['geometry'].centroid.x],
                      icon=folium.DivIcon(html=f'<div style="font-size: 5pt">{row["grid_id"]}</div>')).add_to(m)
    folium.Circle(location=[row.centroid.y, row.centroid.x],
                            radius=3,
                            color='red',
                            fill=True,
                            fill_color='red').add_to(m)
    
# Add grid cells to the map

folium.Circle(location=[start_point.y, start_point.x],
                        radius=30,
                        color='green',
                        fill=True,
                        fill_color='green').add_to(m)
    

folium.Circle(location=[end_point.y, end_point.x],
                        radius=30,
                        color='purple',
                        fill=True,
                        fill_color='purple').add_to(m)


In [65]:
m

## Testing Valhalla Map matching

In [ ]:
gdf = gdf.set_geometry('geometry')
grids = grid_filtered.set_geometry('geometry')
# Realizar um join entre gdf e all_point_counts
joined = gpd.sjoin(grids, gdf, how='inner', predicate='contains')

In [ ]:
#decode an encoded string
def decode(encoded):
  inv = 1.0 / 1e6
  decoded = []
  previous = [0,0]
  i = 0
  #for each byte
  while i < len(encoded):
    #for each coord (lat, lon)
    ll = [0,0]
    for j in [0, 1]:
      shift = 0
      byte = 0x20
      #keep decoding bytes until you have this coord
      while byte >= 0x20:
        byte = ord(encoded[i]) - 63
        i += 1
        ll[j] |= (byte & 0x1f) << shift
        shift += 5
      #get the final value adding the previous offset and remember it for the next
      ll[j] = previous[j] + (~(ll[j] >> 1) if ll[j] & 1 else (ll[j] >> 1))
      previous[j] = ll[j]
    #scale by the precision and chop off long coords also flip the positions so
    #its the far more standard lon,lat instead of lat,lon
    decoded.append([float('%.6f' % (ll[1] * inv)), float('%.6f' % (ll[0] * inv))])
  #hand back the list of coordinates
  return decoded

In [ ]:
# Função para enviar coordenadas para a API trace_route do Valhalla e obter a rota correspondida
import requests
def trace_route_with_valhalla(coordinates):
    url = "http://localhost:8002/trace_route"
    
    while coordinates:
        # Definir o payload JSON para a API Valhalla
        trace_points = [{"lat": lat, "lon": lon} for lon, lat in coordinates]
        payload = {
            "shape": trace_points,
            "costing": "auto",
            "shape_match": "map_snap",
            "format": "osrm"
        }
        
        # Enviar solicitação para a API Valhalla
        response = requests.post(url, json=payload)
        data = response.json()
        
        if response.status_code == 200:
            # Extrair a rota correspondida (polyline)
            route_polyline = data['matchings'][0]['geometry']
            matched_coordinates = decode(route_polyline)
            return matched_coordinates
        elif response.status_code == 400:
            return
        else:
            return
    
    raise Exception("Não foi possível encontrar um segmento válido para as coordenadas fornecidas.")

In [ ]:
routes = {}
for order in joined['ordem'].unique():
    order_df = joined[joined['ordem'] == order].sort_values(by='datahora')
    coordinates = [(centroid.x, centroid.y) for centroid in order_df['centroid']]
    route_coordinates = trace_route_with_valhalla(coordinates)
    routes[order] = route_coordinates

In [ ]:
def calculate_distance(row):
    return geodesic(row['start'], row['end']).kilometers


# Segmentar rotas em segmentos de reta e criar um DataFrame de segmentos

segments_list = []
for order, route in routes.items():
    if route:
        for i in range(len(route) - 1):
            segment = {'ordem': order, 'start': tuple(route[i]), 'end': tuple(route[i+1])}
            segments_list.append(segment)

segments_df = pd.DataFrame(segments_list)

# Contar segmentos únicos por ordem de ônibus
segment_counts = segments_df.groupby(['start', 'end'])['ordem'].nunique().reset_index(name='count')

num_orders = len(routes)
threshold = num_orders / 4
frequent_segments = segment_counts[segment_counts['count'] >= threshold]

frequent_segments['segment_id'] = frequent_segments.index
frequent_segments['distance'] = frequent_segments.apply(calculate_distance, axis=1)
#Remover segmentos maiores que 3 quilômetros
filtered_segments = frequent_segments[frequent_segments['distance'] <= 5]


In [ ]:
# Criar um mapa centralizado no primeiro ponto

map_center = [gdf['geometry'].y.mean(), gdf['geometry'].x.mean()]
m = folium.Map(location=map_center, zoom_start=15)
# Adicionar os centroides ao mapa

# Adicionar segmentos ao mapa
for _, row in filtered_segments.iterrows():
    folium.PolyLine(
        locations=[(row['start'][1], row['start'][0]), (row['end'][1], row['end'][0])],
        color='blue',
        weight=2.5,
        opacity=1,
        popup=f"ID: {row['segment_id']}, Distância: {row['distance']:.2f} km"
    ).add_to(m)

# Adicionar a rota destacada em vermelho
ordem_destacada = list(routes.keys())[0]  # Escolha a primeira ordem para exemplo
# Add grid cells to the map
for _, row in joined[joined['ordem'] == ordem_destacada].iterrows():
    folium.Circle(location=[row.centroid.y, row.centroid.x],
                            radius=3,
                            color='red',
                            fill=True,
                            fill_color='red').add_to(m)
    

    

In [ ]:
m

- Valhalla makes good estimations, but does not work for every line :(

## Draw Trajectories by Interpolation and Median of routes

In [66]:
gdf = gdf.set_geometry('geometry')
grids = grid_filtered.set_geometry('geometry')
# Realizar um join entre gdf e all_point_counts
joined = gpd.sjoin(grids, gdf, how='inner', predicate='contains')

In [240]:
# Função para calcular a distância entre dois pontos
from geopy.distance import geodesic
def calculate_distance(point1, point2):
    return geodesic(point1, point2).meters

# Função para calcular a distância entre dois pontos
def order_centroids(df, start_point, end_point, max_iter=200, max_dist=350, max_travel_dist=5000):
    # Encontrar o ponto mais próximo do ponto inicial
    df['start_distance'] = df['centroid'].apply(lambda x: calculate_distance((x.y, x.x), start_point))
    start_df = df.sort_values(by='start_distance').iloc[0]
    df['end_distance'] = df['centroid'].apply(lambda x: calculate_distance((x.y, x.x), end_point))

    # Ordenar os pontos a partir do ponto inicial
    ordered_centroids = [(start_df['centroid'].y, start_df['centroid'].x)]
    current_point = start_df
    passed_points = {current_point['grid_id']}
    
    while max_iter:
        max_iter -= 1
        next_points = df[(df['datahora'] > current_point['datahora']) & 
                         (~df['grid_id'].isin(passed_points))].sort_values(by='datahora')
        if next_points.empty:
            return (ordered_centroids, 0)
       
        next_point = next_points.iloc[0]

        distance = calculate_distance((current_point['centroid'].y, current_point['centroid'].x), 
                                    (next_point['centroid'].y, next_point['centroid'].x))
        if distance > max_travel_dist:
            print(next_point)
            print(distance)
            return (ordered_centroids, 0)
        if calculate_distance((next_point['centroid'].y, next_point['centroid'].x), end_point) <= max_dist:
            print(next_point)
            print(max_dist)
            return (ordered_centroids, 1)

        passed_points.add(next_point['grid_id'])
        ordered_centroids.append((next_point['centroid'].y, next_point['centroid'].x))
        current_point = next_point

    return (ordered_centroids, 0)
    

In [68]:
# Função para traçar segmentos de reta para um ônibus específico
def trace_routes(df, ordem_id, start_point, end_point):
    bus_df = df[df['ordem'] == ordem_id]
    ordered_centroids = order_centroids(bus_df, start_point, end_point)
    
    # # Traçar segmentos de reta
    # segments = []
    # for i in range(len(ordered_centroids) - 1):
    #     segment = (ordered_centroids[i], ordered_centroids[i + 1])
    #     segments.append(segment)
    
    return ordered_centroids

In [ ]:
end = end_point.y, end_point.x
start = start_point.y, start_point.x

number_bus = joined['ordem'].nunique()

all_routes_ida = {} 
all_routes_volta = {} 
for ordem_id in joined['ordem'].unique():
    route_ida = trace_routes(joined, ordem_id, start, end)  
    route_volta = trace_routes(joined, ordem_id, end, start)        
    if len(route_ida[0]) != 200 and len(route_ida[0]) > 10:
        all_routes_ida[ordem_id] = {'rota': route_ida[0], 'complete': route_ida[1]}

    if len(route_volta[0]) != 200 and len(route_volta[0]) > 10:
        all_routes_volta[ordem_id] = {'rota': route_volta[0], 'complete': route_volta[1]}


In [244]:
# Função para criar um GeoDataFrame de rota como uma única linha

from pyproj import Geod

geod = Geod(ellps="WGS84")

def create_route_gdf(route, complete, route_id):
    line = LineString([(point[1], point[0]) for point in route])
    return gpd.GeoDataFrame({'route_id': [route_id], 'geometry': [line], 'complete': [complete]})

def get_best_route(all_routes):
    # Criar GeoDataFrame de todas as rotas
    all_routes_gdf = pd.concat([create_route_gdf(route['rota'], route['complete'], idx) for idx, route in all_routes.items()], ignore_index=True)
    grids_gdf = gpd.GeoDataFrame(grid_filtered, geometry='geometry')
    # Interseção usando overlay
    intersection_gdf = gpd.overlay(all_routes_gdf, grids_gdf, how='intersection')

    # Contar interseções por rota
    intersection_counts = intersection_gdf.groupby('route_id')['grid_id'].nunique()

    # Calcular o comprimento das linhas das rotas
    all_routes_gdf = all_routes_gdf.set_index('route_id')
    route_lengths = all_routes_gdf['geometry'].map(lambda x: geod.geometry_length(x))
    # Calcular a razão interseções/comprimento para cada rota
    ratio = intersection_counts.divide(route_lengths)
    all_routes_gdf['route_order'] = ratio
    all_routes_gdf = all_routes_gdf.sort_values(by=['complete', 'route_order'], ascending=False)
    route_id = all_routes_gdf.iloc[0].name
    print(route_id)
    return all_routes[route_id]['rota']

In [245]:

best_route = get_best_route(all_routes_ida)

C:\Users\lucas\AppData\Local\Temp\ipykernel_16968\128793895.py:16: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:4326

  intersection_gdf = gpd.overlay(all_routes_gdf, grids_gdf, how='intersection')


B31077


In [247]:
# Criar um mapa centrado na rota do ônibus
m = folium.Map([start_point.y, start_point.x], zoom_start=14)

# Adicionar a rota do ônibus ao mapa]
# Add grid cells to the map
for _, row in grid_filtered.iterrows():
    folium.GeoJson(row.geometry).add_to(m)
    # folium.Marker(location=[row['geometry'].centroid.y, row['geometry'].centroid.x],
    #                   icon=folium.DivIcon(html=f'<div style="font-size: 5pt">{row["grid_id"]}</div>')).add_to(m)
    folium.Circle(location=[row.centroid.y, row.centroid.x],
                            radius=3,
                            color='red',
                            fill=True,
                            popup=row["grid_id"],
                            fill_color='red').add_to(m)




# folium.PolyLine(locations=[(point.y, point.x) for point in centroids_ordenados], color='blue').add_to(m)


folium.PolyLine(locations=[(point[0], point[1]) for point in best_route], color='red').add_to(m)


In [248]:
m

: 